In [1]:
import os
import glob
import time
from datetime import timedelta, datetime
import numpy as np
import pandas as pd
import qgrid

from plotly.graph_objs import Scatter,Layout
import plotly
import plotly.offline as py
import plotly.graph_objs as go
from plotly.subplots import make_subplots

#setting offilne
plotly.offline.init_notebook_mode(connected=True)
import gezi

from projects.feed.rank.monitor.taurus import Taurus

In [2]:
%%html
<style>
.output_wrapper, .output {
    height:auto !important;
    max-height:10000px;  /* your desired max-height here */
}
.output_scroll {
    box-shadow:none !important;
    webkit-box-shadow:none !important;
}
</style>

In [21]:
last_days = 90
start_time = None
end_time = None
# start_time = 20191210
# end_time = 20191220
# abids = [8,15,16]
# abids = [16, 8]
# abids = [16]
# abids = [8, 15]
# abids = [15]
# abids = [8]
abids = [15]
# abids = [11]

assert len(abids) < 2, 'FIXME only 1 abid is ok now, as natural_diff wrong currenlty TODO'
product = 'sgsapp'
# product = 'newmse'

diff_spans_ = {
    8: [20200313, 20200319],
#     12: [20190130, 20200205],
#     11: [20190130, 20200205],
    10: [20200325, 20200331],
    11: [20200325, 20200331],
    15: [20200325, 20200331],
    16: [20200325, 20200331],
    17: [20200325, 20200331],
}
diff_spans = {}
for abid in abids:
  diff_spans[abid] = diff_spans_[abid]

diff_spans = None

In [22]:
worker_daily = Taurus()
worker_daily.init(abids, last_days, 'daily', product=product,
                  diff_spans=diff_spans, start_time=start_time, end_time=end_time)
worker_daily.run()

# for name 1(tuwen,video,small_video,total) 2(quality,total) 3(recommend,relative,total)
def show_daily(name, use_diff=True, quality=False, field=None):
  worker_daily.show(name, quality, field, use_diff=diff_spans != None)

SELECT * FROM feed_abtest_video_type_common_daily 
                WHERE product = 'sgsapp'
                AND abtest in ('4','5','6','15') 
                AND date BETWEEN '20200221' AND '20200522'
                AND video_type in ('0', '1', '2', 'total')
          
26.503352642059326


In [23]:
w = worker_daily
d = worker_daily.ratio2
d = d.sort_values('date', ascending=False)
# pd.set_option('precision', 5)  
names = ['dis_user', 'click_user', 'click', 'duration', 'refresh_times', 'read_files', 'ctr', 'read_ratio', 'dur1', 'dur2', 
         'doc_dur', 'finish_ratio', 'praise', 'favor', 'share']
# d2 = d[d.name!='small_video'].groupby(['name', 'data_obj', 'abtest']).head(6).groupby(['name', 'data_obj', 'abtest'], as_index=False).mean()[['name', 'abtest', 'data_obj', *names]]
d2 = d.groupby(['name', 'data_obj', 'abtest']).head(1).groupby(['name', 'data_obj', 'abtest'], as_index=False).mean()[['name', 'abtest', 'data_obj', *names]]

# qgrid.show_grid(d2)
# d.groupby(['name', 'data_obj', 'abtest']).head(1)

In [6]:
d_ = d2[d2.data_obj=='total_total']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [7]:
d_ = d2[d2.data_obj=='quality_total']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [8]:
d_ = d2[d2.data_obj=='total_relative']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [9]:
w.ratio2[w.ratio2.name=='small_video'][w.ratio2.data_obj=='total_total'][['date', *names]].sort_values('date', ascending=False)

date  dis_user  click_user     click  duration  refresh_times  \
725  20200521  0.015697    0.005874  0.073295  0.059766      -0.012285   
701  20200520  0.009753   -0.016045 -0.045275 -0.014531       0.176886   
677  20200519  0.008192    0.033098  0.083062  0.058972       0.080311   
653  20200518  0.004074    0.027919  0.028303  0.049629       0.013605   
629  20200517 -0.004843    0.054426  0.139995  0.067545       0.121739   
605  20200516  0.006134    0.049226  0.060092 -0.007980      -0.113001   
581  20200515  0.010983    0.017458  0.076805  0.018600      -0.249655   
557  20200514  0.002847    0.012083  0.008699 -0.033973      -0.009879   
533  20200513  0.002443   -0.046028  0.014219  0.046384      -0.058121   
509  20200512  0.004551    0.001904  0.083582  0.084324       0.119789   
485  20200511 -0.000304   -0.013248  0.046832  0.061600       0.020505   
461  20200510 -0.002750   -0.007380 -0.037151 -0.058856      -0.214901   
437  20200509 -0.003947    0.016705  0.282505  0.305643      -0.050776   
413  20200508  0.001885    0.023305  0.072001  0.109809      -0.202243   
389  20200507  0.003026   -0.009967  0.084689  0.053497      -0.276105   
365  20200506 -0.007322    0.023969  0.141442  0.099875       0.043363   
341  20200505 -0.008478    0.026658 -0.016306  0.029978      -0.222488   
317  20200504 -0.017366    0.002432  0.002144 -0.005434      -0.015287   
293  20200503 -0.014878    0.038341 -0.021525  0.042772      -0.030873   
269  20200502 -0.013714    0.017717  0.033334  0.035824      -0.130214   
245  20200501 -0.008433    0.047557  0.019036  0.040674      -0.118658   
221  20200430 -0.003668   -0.007485 -0.013230 -0.017515      -0.169965   
197  20200429  0.004601    0.030142 -0.030209 -0.041347       0.153846   
173  20200428  0.004720    0.041963  0.062681  0.037567       0.174597   
149  20200427  0.007157    0.074976  0.076065  0.101265       0.084507   
125  20200426 -0.000889    0.016568 -0.045692 -0.033735       0.063936   
101  20200425  0.004434    0.002452 -0.151603 -0.149353      -0.172152   
77   20200424  0.011666    0.070627  0.006354  0.024089      -0.061705   
53   20200423  0.005727    0.024905 -0.019935 -0.006401      -0.036342   
29   20200422  0.008109    0.022285 -0.007441 -0.015500       0.053054   
5    20200421  0.002109    0.039018  0.065871  0.058306      -0.019485   

     read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
725    0.056899  0.029984   -0.009605  0.043514  0.054588 -0.016392   
701   -0.054505 -0.056861   -0.025455 -0.024096  0.000899  0.030800   
677    0.074238  0.089333    0.024771  0.050342  0.025259 -0.022219   
653    0.024031  0.018762    0.023765  0.045333  0.021311  0.019712   
629    0.145696  0.124907    0.059491  0.072955  0.012086 -0.062149   
605    0.053428  0.036344    0.042777 -0.014231 -0.053156 -0.064228   
581    0.065051  0.055901    0.006486  0.007532  0.001942 -0.052624   
557    0.006115  0.006484    0.009282 -0.036456 -0.044599 -0.042422   
533    0.011535  0.031034   -0.048346  0.043555  0.097884  0.032560   
509    0.078786  0.054857   -0.002590  0.079549  0.081602  0.001241   
485    0.047090  0.036436   -0.012841  0.061879  0.075081  0.014110   
461   -0.034422 -0.030547   -0.004541 -0.056195 -0.052107 -0.022596   
437    0.287968  0.256158    0.020858  0.311193  0.285001  0.017964   
413    0.070170  0.047739    0.021415  0.107904  0.085253  0.035491   
389    0.081482  0.086936   -0.012807  0.050461  0.064474 -0.028182   
365    0.150019  0.127851    0.031524  0.108226  0.074332 -0.036433   
341   -0.007732 -0.025376    0.035472  0.038882  0.003454  0.046663   
317    0.019780  0.006754    0.020239  0.012105 -0.008492 -0.007874   
293   -0.006660 -0.006746    0.054057  0.058630  0.005220  0.066383   
269    0.047611  0.033712    0.031819  0.050194  0.018249  0.001875   
245    0.027986  0.015578    0.056552  0.049880 -0.005817  0.021723   
221   -0.009609 -0.011655   -0.003854 -0.013783 -0.010103 -0.004310   
197   -

In [10]:
w.df[w.df.name=='total'][w.df.data_obj=='total_total']

product_name      date   name     data_obj  abtest        id         dis  \
11        sgsapp  20200421  total  total_total      15  22269303  32532290.0   
35        sgsapp  20200422  total  total_total      15  22391511  32411034.0   
59        sgsapp  20200423  total  total_total      15  22514175  32000714.0   
83        sgsapp  20200424  total  total_total      15  22641563  31854134.0   
107       sgsapp  20200425  total  total_total      15  22772141  32093036.0   
131       sgsapp  20200426  total  total_total      15  22902157  31555018.0   
155       sgsapp  20200427  total  total_total      15  23028675  32500946.0   
179       sgsapp  20200428  total  total_total      15  23154443  32466278.0   
203       sgsapp  20200429  total  total_total      15  23280783  32941830.0   
227       sgsapp  20200430  total  total_total      15  23406521  32985664.0   
251       sgsapp  20200501  total  total_total      15  23532825  33193434.0   
275       sgsapp  20200502  total  total_total      15  23659227  32784508.0   
299       sgsapp  20200503  total  total_total      15  23784767  32479144.0   
323       sgsapp  20200504  total  total_total      15  23911193  32846128.0   
347       sgsapp  20200505  total  total_total      15  24036841  31864974.0   
371       sgsapp  20200506  total  total_total      15  24162237  32003674.0   
395       sgsapp  20200507  total  total_total      15  24286019  32292142.0   
419       sgsapp  20200508  total  total_total      15  24411681  35341490.0   
443       sgsapp  20200509  total  total_total      15  24538227  35657392.0   
467       sgsapp  20200510  total  total_total      15  24663165  35544552.0   
491       sgsapp  20200511  total  total_total      15  24789139  33570624.0   
515       sgsapp  20200512  total  total_total      15  24914333  34070422.0   
539       sgsapp  20200513  total  total_total      15  25038965  33371882.0   
563       sgsapp  20200514  total  total_total      15  25164115  34454586.0   
587       sgsapp  20200515  total  total_total      15  25289451  35078828.0   
611       sgsapp  20200516  total  total_total      15  25414143  36355378.0   
635       sgsapp  20200517  total  total_total      15  25539251  37488126.0   
659       sgsapp  20200518  total  total_total      15  25667407  35135244.0   
683       sgsapp  20200519  total  total_total      15  25799075  34323516.0   
707       sgsapp  20200520  total  total_total      15  25930819  33810586.0   
731       sgsapp  20200521  total  total_total      15  26062417  33845880.0   

     dis_user  refresh_times   real_dis  ...       ctr  real_ctr  read_ratio  \
11   305178.0      1367164.0  7791094.0  ...  0.055098  0.230064    0.320849   
35   303628.0      1375596.0  7810224.0  ...  0.054005  0.224110    0.316684   
59   301884.0      1369078.0  7789226.0  ...  0.054979  0.225870    0.323435   
83   304022.0      1368084.0  7798758.0  ...  0.056540  0.230940    0.326674   
107  305170.0      1370148.0  7855094.0  ...  0.057510  0.234965    0.325274   
131  300542.0      1359520.0  7811766.0  ...  0.056857  0.229669    0.326071   
155  299254.0      1368638.0  7822664.0  ...  0.058108  0.241424    0.330856   
179  300774.0      1363280.0  7731656.0  ...  0.056333  0.236552    0.331611   
203  301976.0      1374266.0  7734246.0  ...  0.056383  0.240148    0.328695   
227  307372.0      1387198.0  7906074.0  ...  0.055456  0.231375    0.330505   
251  307882.0      1395688.0  7927024.0  ...  0.057496  0.240757    0.323377   
275  299770.0      1356490.0  7830116.0  ...  0.055046  0.230477    0.320926   
299  306118.0      1361170.0  7699628.0  ...  0.053466  0.225533    0.323522   
323  305928.0      1367324.0  7812080.0  ...  0.052425  0.220421    0.329947   
347  299746.0      1339622.0  7604722.0  ...  0.051767  0.216910    0.326203   
371  297034.0      1335568.0  7608450.0  ...  0.052125  0.219255    0.332999   
395  295328.0      1324942.0  7656860.0  ...  0.054730  0.230817    0.339047   
419

In [11]:
w.base[w.base.name=='total'][w.base.data_obj=='total_total']

product_name      date   name     data_obj  abtest          id  \
11        sgsapp  20200421  total  total_total     5.0  22269383.0   
35        sgsapp  20200422  total  total_total     5.0  22391591.0   
59        sgsapp  20200423  total  total_total     5.0  22514255.0   
83        sgsapp  20200424  total  total_total     5.0  22641643.0   
107       sgsapp  20200425  total  total_total     5.0  22772221.0   
131       sgsapp  20200426  total  total_total     5.0  22902237.0   
155       sgsapp  20200427  total  total_total     5.0  23028755.0   
179       sgsapp  20200428  total  total_total     5.0  23154523.0   
203       sgsapp  20200429  total  total_total     5.0  23280863.0   
227       sgsapp  20200430  total  total_total     5.0  23406601.0   
251       sgsapp  20200501  total  total_total     5.0  23532905.0   
275       sgsapp  20200502  total  total_total     5.0  23659307.0   
299       sgsapp  20200503  total  total_total     5.0  23784847.0   
323       sgsapp  20200504  total  total_total     5.0  23911273.0   
347       sgsapp  20200505  total  total_total     5.0  24036921.0   
371       sgsapp  20200506  total  total_total     5.0  24162317.0   
395       sgsapp  20200507  total  total_total     5.0  24286099.0   
419       sgsapp  20200508  total  total_total     5.0  24411761.0   
443       sgsapp  20200509  total  total_total     5.0  24538307.0   
467       sgsapp  20200510  total  total_total     5.0  24663245.0   
491       sgsapp  20200511  total  total_total     5.0  24789219.0   
515       sgsapp  20200512  total  total_total     5.0  24914413.0   
539       sgsapp  20200513  total  total_total     5.0  25039045.0   
563       sgsapp  20200514  total  total_total     5.0  25164195.0   
587       sgsapp  20200515  total  total_total     5.0  25289531.0   
611       sgsapp  20200516  total  total_total     5.0  25414223.0   
635       sgsapp  20200517  total  total_total     5.0  25539331.0   
659       sgsapp  20200518  total  total_total     5.0  25667487.0   
683       sgsapp  20200519  total  total_total     5.0  25799155.0   
707       sgsapp  20200520  total  total_total     5.0  25930899.0   
731       sgsapp  20200521  total  total_total     5.0  26062497.0   

              dis       dis_user  refresh_times      real_dis  ...       ctr  \
11   3.198206e+07  304687.333333   1.349337e+06  7.629531e+06  ...  0.055343   
35   3.180094e+07  303030.666667   1.357545e+06  7.632697e+06  ...  0.053918   
59   3.152692e+07  300702.000000   1.353117e+06  7.629526e+06  ...  0.054806   
83   3.155335e+07  303350.666667   1.359590e+06  7.681170e+06  ...  0.056324   
107  3.202331e+07  303807.333333   1.362755e+06  7.756025e+06  ...  0.057190   
131  3.161330e+07  300152.666667   1.357997e+06  7.776681e+06  ...  0.056729   
155  3.212145e+07  298670.000000   1.356990e+06  7.709213e+06  ...  0.056890   
179  3.218219e+07  298386.000000   1.357130e+06  7.648084e+06  ...  0.056123   
203  3.254873e+07  301987.333333   1.365873e+06  7.635293e+06  ...  0.056504   
227  3.307710e+07  306892.666667   1.388746e+06  7.824727e+06  ...  0.056469   
251  3.319240e+07  307132.666667   1.393491e+06  7.897407e+06  ...  0.057211   
275  3.284029e+07  301572.666667   1.370641e+06  7.826905e+06  ...  0.055951   
299  3.273676e+07  305497.333333   1.375079e+06  7.765406e+06  ...  0.054675   
323  3.271596e+07  305608.000000   1.373638e+06  7.784498e+06  ...  0.052894   
347  3.201679e+07  299544.666667   1.344637e+06  7.592921e+06  ...  0.052461   
371  3.213743e+07  296448.666667   1.337729e+06  7.586841e+06  ...  0.052665   
395  3.215086e+07  294090.666667   1.326997e+06  7.649473e+06  ...  0.054256   
419  3.501428e+07  302585.333333   1.343476e+06  7.630741e+06  ...  0.049520   
443  3.532988e+07  308169.333333   1.348184e+06  7.729561e+06  ...  0.051030   
467  3.529077e+07  309341.333333   1.353873e+06  7.792817e+06  ...  0.049630   
491  3.339256e+07  298070.666667   1.288648e+06  7.255446e+06  ...  0.048438   
515

In [26]:
show_daily('small_video_total_relative')

refresh_times with same vals ignore


In [13]:
show_daily('total_quality_total')

In [14]:
show_daily('tuwen_total_total')

In [15]:
show_daily('video_total_recommend')

In [16]:
show_daily('tuwen_total_recommend')

In [17]:
show_daily('total_quality_total')

In [18]:
show_daily('tuwen_total_total')

In [19]:
w.ratio

product_name      date         name           data_obj  abtest        id  \
0         sgsapp  20200421  small_video  quality_recommend      15 -0.000004   
1         sgsapp  20200421  small_video   quality_relative      15 -0.000004   
2         sgsapp  20200421  small_video      quality_total      15 -0.000004   
3         sgsapp  20200421  small_video    total_recommend      15 -0.000004   
4         sgsapp  20200421  small_video     total_relative      15 -0.000004   
..           ...       ...          ...                ...     ...       ...   
739       sgsapp  20200521        video   quality_relative      15 -0.000003   
740       sgsapp  20200521        video      quality_total      15 -0.000003   
741       sgsapp  20200521        video    total_recommend      15 -0.000003   
742       sgsapp  20200521        video     total_relative      15 -0.000003   
743       sgsapp  20200521        video        total_total      15 -0.000003   

          dis  dis_user  refresh_times  real_dis  ...       ctr  real_ctr  \
0    0.020193  0.002105      -0.057592  0.033996  ...  0.045325  0.032964   
1    0.057648  0.031699       0.000000  0.000000  ...  0.011113  0.064382   
2    0.023095  0.002539       0.067518  0.034036  ...  0.038557  0.028516   
3    0.017869  0.001886       0.011401  0.030710  ...  0.016192  0.004123   
4    0.054933  0.038278       0.000000  0.000000  ...  0.024688  0.076695   
..        ...       ...            ...       ...  ...       ...       ...   
739  0.021519  0.010425       0.000000  0.000000  ...  0.004841  0.026565   
740  0.018976  0.012098       0.024380  0.007672  ...  0.003547  0.014735   
741  0.004310  0.004327      -0.000668  0.004927  ...  0.000573  0.000042   
742  0.020692  0.004276       0.000000  0.380922  ...  0.003605 -0.283566   
743  0.013850  0.004139      -0.003569  0.003953  ...  0.006274  0.016143   

     read_ratio      dur1      dur2  finish_ratio  read_files   doc_dur  \
0      0.056422  0.043668 -0.011595      0.003095    0.066284 -0.020425   
1      0.016760  0.100275  0.084503      0.044827    0.031339  0.057571   
2      0.045830  0.113823  0.065648      0.036856    0.061417  0.041980   
3      0.050405  0.029957 -0.019768     -0.008760    0.033606 -0.004863   
4      0.015330  0.026147  0.012364      0.006771    0.036270 -0.013817   
..          ...       ...       ...           ...         ...       ...   
739   -0.000965  0.016573  0.017584      0.006057    0.015878  0.000631   
740   -0.006950  0.007452  0.014497      0.011517    0.010383 -0.002973   
741   -0.002112 -0.005625 -0.003527     -0.006277    0.000677 -0.006300   
742    0.012770  0.025388  0.012432      0.006665    0.020021  0.005238   
743   -0.001963  0.016679  0.018675      0.003159    0.016049  0.000594   

      refresh  refresh2  
0   -0.059722 -0.111734  
1   -0.031159 -0.047582  
2    0.064753  0.017335  
3    0.009227 -0.039688  
4   -0.037015 -0.051708  
..        ...       ...  
739 -0.010367 -0.009404  
740  0.012104  0.019178  
741 -0.004969 -0.002897  
742 -0.004259 -0.016842  
743 -0.007671 -0.005761  

[744 rows x 33 columns]